In [3]:
import os
from tqdm import tqdm
import glob
from astropy.io import fits
import os
from astropy.io import fits
from astropy.wcs import WCS
from spherical_geometry.polygon import SphericalPolygon
import os
from astropy.io import fits
from astropy.wcs import WCS
from spherical_geometry.polygon import SphericalPolygon
from sklearn.cluster import AgglomerativeClustering
import matplotlib.pyplot as plt
import pandas as pd
from astropy.io import fits
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np

"""

Use this code after downloading all SDSS data first, using the file
titled sdss_downloading.

"""

def get_all_fits_files(root_dir):
    # Use glob to recursively find all .fits files
    pattern = os.path.join(root_dir, '**', '*.fits')
    fits_files = glob.glob(pattern, recursive=True)
    return fits_files

valid_fits_paths = get_all_fits_files('./data')
len(valid_fits_paths)

522

In [11]:
"""
Computes a spherical polygon object for each FITS file using WCS coordinates.
Stores each in a list.

"""


# Initialize the list of confirmed FITS paths
confirmed_fits_paths = []

all_polys = []

for i in tqdm(range(len(valid_fits_paths))):
    path1 = valid_fits_paths[i]
    try:
        with fits.open(path1) as hdul:
            hdul[0].data = hdul[0].data[0, 0]
            wcs1a = WCS(hdul[0].header)
            shape1a = sorted(tuple(wcs1a.pixel_shape))[:2]
            footprint1a = wcs1a.calc_footprint(axes=shape1a)
            poly1a = SphericalPolygon.from_radec(footprint1a[:, 0], footprint1a[:, 1])
            all_polys.append(poly1a)
    except Exception as e:
        print(e)
        continue

  9%|███▊                                      | 47/522 [00:28<06:45,  1.17it/s]WARNING: FITSFixedWarning: RADECSYS= 'ICRS ' / International Celestial Reference Sys 
the RADECSYS keyword is deprecated, use RADESYSa. [astropy.wcs.wcs]
100%|█████████████████████████████████████████| 522/522 [06:48<00:00,  1.28it/s]


In [13]:
latitudes = []
longitudes = []

"""
Get a list of all RA and DEC into a list before filtering.

"""

for poly in tqdm(all_polys):
    pts = list(poly.to_radec())[0]
    ra = pts[0][0]
    dec = pts[1][0]
    
    longitudes.append(ra)
    latitudes.append(dec)

100%|██████████████████████████████████████| 522/522 [00:00<00:00, 17983.71it/s]


In [14]:
n_points = len(latitudes)

# Repeat each point n_points times for lat1, lon1
lat1 = np.repeat(latitudes, n_points)
lon1 = np.repeat(longitudes, n_points)

# Tile the whole array n_points times for lat2, lon2
lat2 = np.tile(latitudes, n_points)
lon2 = np.tile(longitudes, n_points)

# Calculates angular separation between two spherical coords
# This can be lat/lon or ra/dec
# Taken from astropy
def angular_separation_deg(lon1, lat1, lon2, lat2):
    lon1 = np.deg2rad(lon1)
    lon2 = np.deg2rad(lon2)
    lat1 = np.deg2rad(lat1)
    lat2 = np.deg2rad(lat2)
    
    sdlon = np.sin(lon2 - lon1)
    cdlon = np.cos(lon2 - lon1)
    slat1 = np.sin(lat1)
    slat2 = np.sin(lat2)
    clat1 = np.cos(lat1)
    clat2 = np.cos(lat2)

    num1 = clat2 * sdlon
    num2 = clat1 * slat2 - slat1 * clat2 * cdlon
    denominator = slat1 * slat2 + clat1 * clat2 * cdlon

    return np.rad2deg(np.arctan2(np.hypot(num1, num2), denominator))

# Compute the pairwise angular separations
angular_separations = angular_separation_deg(lon1, lat1, lon2, lat2)

# Reshape the result into a matrix form
angular_separations_matrix = angular_separations.reshape(n_points, n_points)

def check_symmetric(a, rtol=1e-05, atol=1e-07):
    return np.allclose(a, a.T, rtol=rtol, atol=atol)

print("Symmetric?")
print(check_symmetric(angular_separations_matrix))
print(angular_separations_matrix.shape)

Symmetric?
True
(522, 522)


In [19]:
SDSS_FOV = 0.088

THRESH = SDSS_FOV * 4

"""
Initial clustering phase using just RA DEC, not WCS polygon footprints.

"""

clustering = AgglomerativeClustering(n_clusters=None, metric='precomputed', linkage='single', distance_threshold=THRESH)
labels = clustering.fit_predict(angular_separations_matrix)

In [24]:
failed_labels = []
failed_paths = []

for label in tqdm(np.unique(labels)):
    polys = [(all_polys[i], valid_fits_paths[i]) for i in range(len(labels)) if labels[i] == label]
    if len(polys) > 1:
        total_poly = polys[0][0]
        for i in range(1, len(polys)):
            new_poly = polys[i][0]
            new_path = polys[i][1]
            if total_poly.intersects_poly(new_poly):
                union_over_max = total_poly.intersection(new_poly).area() / new_poly.area()
                print(f"FAIL label: {label}, i: {i} IoU: {union_over_max}")
                failed_labels.append(label)
                failed_paths.append(new_path)
                continue
            else:
                total_poly = total_poly.union(new_poly)

  3%|█▍                                        | 13/377 [00:00<00:21, 16.71it/s]

FAIL label: 10, i: 1 IoU: 0.25944657797281734


  8%|███▏                                      | 29/377 [00:01<00:15, 21.76it/s]

FAIL label: 23, i: 2 IoU: 0.4090236242653364


  9%|███▉                                      | 35/377 [00:02<00:15, 22.08it/s]

...

FAIL label: 91, i: 2 IoU: 0.30092583437382314
FAIL label: 106, i: 1 IoU: 0.5437761463648566
FAIL label: 110, i: 1 IoU: 0.978096219321612


 43%|█████████████████▎                      | 163/377 [00:04<00:01, 124.92it/s]

FAIL label: 137, i: 1 IoU: 0.5768840711253176
FAIL label: 138, i: 1 IoU: 0.426858068191846
FAIL label: 142, i: 1 IoU: 1.0
FAIL label: 151, i: 1 IoU: 0.6865076393310577
FAIL label: 162, i: 1 IoU: 0.40902362440677925


100%|█████████████████████████████████████████| 377/377 [00:04<00:00, 82.43it/s]

FAIL label: 166, i: 2 IoU: 0.3312197305714273


In [18]:
failed_paths

['./data/cube_center_run4203_camcol6_f746_73-5-800-800.fits',
 './data/cube_center_run2700_camcol2_f56_86-5-800-800.fits',
 './data/cube_center_run4198_camcol6_f243_3-5-800-800.fits',
 './data/cube_center_run5658_camcol2_f33_25-5-800-800.fits',
 './data/cube_center_run4933_camcol2_f695_81-5-800-800.fits',
 './data/cube_center_run2709_camcol5_f236_72-5-800-800.fits',
 './data/cube_center_run5637_camcol4_f385_1-5-800-800.fits',
 './data/cube_center_run5759_camcol4_f118_72-5-800-800.fits',
 './data/cube_center_run2700_camcol5_f163_86-5-800-800.fits',
 './data/cube_center_run3434_camcol4_f456_34-5-800-800.fits',
 './data/cube_center_run5792_camcol6_f342_73-5-800-800.fits',
 './data/cube_center_run5918_camcol5_f278_69-5-800-800.fits',
 './data/cube_center_run4128_camcol3_f475_1-5-800-800.fits',
 './data/cube_center_run5590_camcol2_f272_56-5-800-800.fits',
 './data/cube_center_run5836_camcol6_f545_52-5-800-800.fits',
 './data/cube_center_run4933_camcol3_f554_85-5-800-800.fits',
 './data/cube

In [29]:
os.listdir('./splits')

['tiny_train.jsonl', 'full_train.jsonl', 'full_test.jsonl', 'tiny_test.jsonl']

In [42]:
import pandas as pd

# Path to the JSONL file
file_path = './splits/full_train.jsonl'

# Read the JSONL file into a DataFrame
df_train = pd.read_json(file_path, lines=True)

# Path to the JSONL file
file_path = './splits/full_test.jsonl'

# Read the JSONL file into a DataFrame
df_test = pd.read_json(file_path, lines=True)

In [49]:
df = pd.concat([df_train, df_test])
df = df[~df['image'].isin(failed_paths)]

In [54]:
import pandas as pd
from sklearn.model_selection import train_test_split

# Assuming df is your DataFrame
# df = pd.DataFrame(...) # Your DataFrame should already be defined

# Perform an 85/15 train-test split
train_df, test_df = train_test_split(df, test_size=0.15, random_state=42)

# Save the train and test DataFrames to CSV files
train_df.to_csv('full_train.csv', index=False)
test_df.to_csv('full_test.csv', index=False)

print("Train and test datasets have been saved to 'train_data.csv' and 'test_data.csv'.")

Train and test datasets have been saved to 'train_data.csv' and 'test_data.csv'.


In [55]:
import pandas as pd

# Path to the JSONL file
file_path = './splits/tiny_train.jsonl'

# Read the JSONL file into a DataFrame
df_train = pd.read_json(file_path, lines=True)

# Path to the JSONL file
file_path = './splits/tiny_test.jsonl'

# Read the JSONL file into a DataFrame
df_test = pd.read_json(file_path, lines=True)

print(len(df_train))
print(len(df_test))

# Save the train and test DataFrames to CSV files
df_train.to_csv('tiny_train.csv', index=False)
df_test.to_csv('tiny_test.csv', index=False)

print("Train and test datasets have been saved to 'train_data.csv' and 'test_data.csv'.")

2
1
Train and test datasets have been saved to 'train_data.csv' and 'test_data.csv'.


In [59]:
import pandas as pd

names = ["./splits/tiny_train", "./splits/tiny_test", "./splits/full_train", "./splits/full_test"]

for name in names:

    # Step 1: Load the CSV file into a DataFrame
    csv_file_path = f'{name}.csv'  # Replace with your actual CSV file path
    df = pd.read_csv(csv_file_path)

    # Step 2: Save the DataFrame as a JSONL file
    jsonl_file_path = f'{name}.jsonl'  # Replace with your desired output file path
    df.to_json(jsonl_file_path, orient='records', lines=True)

    print(f"CSV file has been converted and saved as JSONL at {jsonl_file_path}")

CSV file has been converted and saved as JSONL at ./splits/tiny_train.jsonl
CSV file has been converted and saved as JSONL at ./splits/tiny_test.jsonl
CSV file has been converted and saved as JSONL at ./splits/full_train.jsonl
CSV file has been converted and saved as JSONL at ./splits/full_test.jsonl
